# Background

---

A Supermarket selling various items, ranging from common household supplies (meats, fish, and fruits) to specific commodities (wines, sweets, and golds) towards various kinds of individual customers. Clients of this Supermarket may purchase the products directly in stores or via other media, namely website and catalog. This Supermarket also has done six promotional campaigns to their customers offering discounted price.

Apparently the conversion rate (percentage of customers accepting those discount offerings) are persistently low from one campaign to another. This questions the effectivity of Supermarket's campaign process. Supermarket's Marketing Manager as our stakeholder then tasked us, the data analyst, to find a new approach that can solve this "low-rate" problem.

### <i>Problem Statement</i>

Based on this condition, we can see there may be a mismatch between customers' profile, products they bought, and where they purchase it against promotional campaigns done by Supermarket. Therefore, the question we are going to answer is as follows:

<b>How is the characteristics of these three groups and what is the suitable campaign offerings based on the following findings?</b>

# Data Preparation

---

To answer the questions above, we will begin by preparing Supermarket's data provided <a href="https://drive.google.com/drive/folders/1WodnBbuYTvsF0-6HTuQABQ0KCS31lqbK">here</a>.

In [62]:
# Importing required modules for this analysis
from pdfminer.high_level import extract_text
import pandas as pd
import numpy as np
import altair as alt

In [63]:
# Option setting (for ease of viewing later on):
# Setting maximum columns displayed to be more than dataframe's columns to view truncated columns
pd.options.display.max_columns = 50

# Setting maximum column width to see more of truncated values
pd.options.display.max_colwidth = 100

pd.set_option('display.precision', 3)

Here are the top 5 and bottom 5 lines of the `Supermarket Customer` dataset:

In [64]:
# Loading dataset
df = pd.read_csv("Supermarket Customers.csv", delimiter='\t')
display(df.head(), df.tail())

ID  Year_Birth   Education Marital_Status   Income  Kidhome  Teenhome  \
0  5524        1957  Graduation         Single  58138.0        0         0   
1  2174        1954  Graduation         Single  46344.0        1         1   
2  4141        1965  Graduation       Together  71613.0        0         0   
3  6182        1984  Graduation       Together  26646.0        1         0   
4  5324        1981         PhD        Married  58293.0        1         0   

  Dt_Customer  Recency  MntWines  MntFruits  MntMeatProducts  MntFishProducts  \
0  04-09-2012       58       635         88              546              172   
1  08-03-2014       38        11          1                6                2   
2  21-08-2013       26       426         49              127              111   
3  10-02-2014       26        11          4               20               10   
4  19-01-2014       94       173         43              118               46   

   MntSweetProducts  MntGoldProds  NumDealsPurchases  NumWebPurchases  \
0                88            88                  3                8   
1                 1             6                  2                1   
2                21            42                  1                8   
3                 3             5                  2                2   
4                27            15                  5                5   

   NumCatalogPurchases  NumStorePurchases  NumWebVisitsMonth  AcceptedCmp3  \
0                   10                  4                  7             0   
1                    1                  2                  5             0   
2                    2                 10                  4             0   
3                    0                  4                  6             0   
4                    3                  6                  5             0   

   AcceptedCmp4  AcceptedCmp5  AcceptedCmp1  AcceptedCmp2  Complain  \
0             0             0             0             0         0   
1             0             0             0             0         0   
2             0             0             0             0         0   
3             0             0             0             0         0   
4             0             0             0             0         0   

   Z_CostContact  Z_Revenue  Response  
0              3         11         1  
1              3         11         0  
2              3         11         0  
3              3         11         0  
4              3         11         0

ID  Year_Birth   Education Marital_Status   Income  Kidhome  \
2235  10870        1967  Graduation        Married  61223.0        0   
2236   4001        1946         PhD       Together  64014.0        2   
2237   7270        1981  Graduation       Divorced  56981.0        0   
2238   8235        1956      Master       Together  69245.0        0   
2239   9405        1954         PhD        Married  52869.0        1   

      Teenhome Dt_Customer  Recency  MntWines  MntFruits  MntMeatProducts  \
2235         1  13-06-2013       46       709         43              182   
2236         1  10-06-2014       56       406          0               30   
2237         0  25-01-2014       91       908         48              217   
2238         1  24-01-2014        8       428         30              214   
2239         1  15-10-2012       40        84          3               61   

      MntFishProducts  MntSweetProducts  MntGoldProds  NumDealsPurchases  \
2235               42               118           247                  2   
2236                0                 0             8                  7   
2237               32                12            24                  1   
2238               80                30            61                  2   
2239                2                 1            21                  3   

      NumWebPurchases  NumCatalogPurchases  NumStorePurchases  \
2235                9                    3                  4   
2236                8                    2                  5   
2237                2                    3                 13   
2238                6                    5                 10   
2239                3                    1                  4   

      NumWebVisitsMonth  AcceptedCmp3  AcceptedCmp4  AcceptedCmp5  \
2235                  5             0             0             0   
2236                  7             0             0             0   
2237                  6             0             1             0   
2238                  3             0             0             0   
2239                  7             0             0             0   

      AcceptedCmp1  AcceptedCmp2  Complain  Z_CostContact  Z_Revenue  Response  
2235             0             0         0              3         11         0  
2236             1             0         0              3         11         0  
2237             0             0         0              3         11         0  
2238             0             0         0              3         11         0  
2239             0             0         0              3         11         1

The data consist of Supermarket's customer information regarding their demographic (`People`), spending amount (`Products`), offering acceptance (`Promotion`), and purchasing media (`Place`). These are organized into columns according to `Supermarket Customers Data Dictionary` below:

In [65]:
# Loading data dictionary
dataDict = extract_text("Supermarket Customers Data Dictionary.pdf")
print(dataDict)

Supermarket Customers Data Dictionary

People

● ID: Customer's unique identifier
● Year_Birth: Customer's birth year
● Education: Customer's education level
● Marital_Status: Customer's marital status
● Income: Customer's yearly household income
● Kidhome: Number of children in customer's household
● Teenhome: Number of teenagers in customer's household
● Dt_Customer: Date of customer's enrollment with the company
● Recency: Number of days since customer's last purchase
● Complain: 1 if the customer complained in the last 2 years, 0 otherwise

Products

● MntWines: Amount spent on wine in last 2 years
● MntFruits: Amount spent on fruits in last 2 years
● MntMeatProducts: Amount spent on meat in last 2 years
● MntFishProducts: Amount spent on fish in last 2 years
● MntSweetProducts: Amount spent on sweets in last 2 years
● MntGoldProds: Amount spent on gold in last 2 years

Promotion

● NumDealsPurchases: Number of purchases made with a discount
● AcceptedCmp1: 1 if the customer accept

Based on these, we may conclude that our data are:
* <b>Reliable and Comprehensive</b>: the data are unbiased and credible. They may be regarded as complete and accurate, because we can infer the problems from data provided, and they also provide an accurate representation of Supermarket Customers' population. 
* <b>Original</b>: no information provided regarding original provider of this dataset; whether it comes directly from Supermarket or other second or third-party sources.
* <b>Current</b>: no information provided regarding newness of this dataset; whether this data is up-to-date or not.
* <b>Cited</b>: no information provided regarding citation of this dataset; we cannot infer who created this data, when was the data last refreshed, etc.
* No information provided regarding licensing, privacy, security, and accesibility of this data; we obtain this dataset freely without any restrictions whatsoever.

# Data Auditing

---

We will assess how Supermarket Customers data is fit for this analyzing purpose. This involves profiling the data and evaluating the impact of poor quality data towards our analysis, which will be handled in the next stage.

In [66]:
# Performing dataset audit
print(f'Dataset Rows, Columns: {df.shape}')

pd.DataFrame({
    'Name': df.columns.values,
    'Type': df.dtypes.values,
    'N/A (n)': df.isna().sum(),
    'N/A (%)': df.isna().mean().values * 100,
    'Unique': df.nunique().values,
    'Sample': [df[column].unique() for column in df.columns]
}).reset_index()\
    .drop(['index'], axis=1)

Dataset Rows, Columns: (2240, 29)


Name     Type  N/A (n)  N/A (%)  Unique  \
0                    ID    int64        0    0.000    2240   
1            Year_Birth    int64        0    0.000      59   
2             Education   object        0    0.000       5   
3        Marital_Status   object        0    0.000       8   
4                Income  float64       24    1.071    1974   
5               Kidhome    int64        0    0.000       3   
6              Teenhome    int64        0    0.000       3   
7           Dt_Customer   object        0    0.000     663   
8               Recency    int64        0    0.000     100   
9              MntWines    int64        0    0.000     776   
10            MntFruits    int64        0    0.000     158   
11      MntMeatProducts    int64        0    0.000     558   
12      MntFishProducts    int64        0    0.000     182   
13     MntSweetProducts    int64        0    0.000     177   
14         MntGoldProds    int64        0    0.000     213   
15    NumDealsPurchases    int64        0    0.000      15   
16      NumWebPurchases    int64        0    0.000      15   
17  NumCatalogPurchases    int64        0    0.000      14   
18    NumStorePurchases    int64        0    0.000      14   
19    NumWebVisitsMonth    int64        0    0.000      16   
20         AcceptedCmp3    int64        0    0.000       2   
21         AcceptedCmp4    int64        0    0.000       2   
22         AcceptedCmp5    int64        0    0.000       2   
23         AcceptedCmp1    int64        0    0.000       2   
24         AcceptedCmp2    int64        0    0.000       2   
25             Complain    int64        0    0.000       2   
26        Z_CostContact    int64        0    0.000       1   
27            Z_Revenue    int64        0    0.000       1   
28             Response    int64        0    0.000       2   

                                                                                                 Sample  
0   [5524, 2174, 4141, 6182, 5324, 7446, 965, 6177, 4855, 5899, 1994, 387, 2125, 8180, 2569, 2114, 9...  
1   [1957, 1954, 1965, 1984, 1981, 1967, 1971, 1985, 1974, 1950, 1983, 1976, 1959, 1952, 1987, 1946,...  
2                                                            [Graduation, PhD, Master, Basic, 2n Cycle]  
3                                     [Single, Together, Married, Divorced, Widow, Alone, Absurd, YOLO]  
4   [58138.0, 46344.0, 71613.0, 26646.0, 58293.0, 62513.0, 55635.0, 33454.0, 30351.0, 5648.0, nan, 7...  
5                                                                                             [0, 1, 2]  
6                                                                                             [0, 1, 2]  
7   [04-09-2012, 08-03-2014, 21-08-2013, 10-02-2014, 19-01-2014, 09-09-2013, 13-11-2012, 08-05-2013,...  
8   [58, 38, 26, 94, 16, 34, 32, 19, 68, 11, 59, 82, 53, 23, 51, 20, 91, 86, 41, 42, 63, 0, 69, 89, ...  
9   [635, 11, 426, 173, 520, 235, 76, 14, 28, 5, 6, 194, 233, 3, 1006, 53, 84, 1012, 4, 86, 1, 867, ...  
10  [88, 1, 49, 4, 43, 42, 65, 10, 0, 5, 16, 61, 2, 14, 22, 80, 17, 3, 100, 12, 34, 8, 76, 11, 164, ...  
11  [546, 6, 127, 20, 118, 98, 164, 56, 24, 11, 480, 53, 17, 115, 19, 38, 498, 73, 1725, 86, 102, 27...  
12  [172, 2, 111, 10, 46, 0, 50, 3, 1, 11, 225, 6, 59, 150, 30, 69, 21, 39, 15, 20, 34, 33, 119, 160...  
13  [88, 1, 21, 3, 27, 42, 49, 2, 112, 5, 68, 13, 12, 16, 24, 38, 0, 32, 6, 263, 66, 22, 8, 7, 178, ...  
14  [88, 6, 42, 5, 15, 14, 27, 23, 2, 13, 1, 16, 30, 45, 4, 28, 176, 39, 48, 19, 99, 41, 362, 10, 0,...  
15                                                   [3, 2, 1, 5, 4, 15, 7, 0, 6, 9, 12, 8, 10, 13, 11]  
16                                                   [8, 1, 2, 5, 6, 7, 4, 3, 11, 0, 27, 10, 9, 23, 25]  
17                                                       [10, 1, 2, 0, 3, 4, 6, 28, 9, 5, 8, 7, 11, 22]  
18                                                       [4, 2, 10, 6, 7, 0, 3, 8, 5, 12, 9, 13, 11, 1]  
19                                    

In [67]:
# Performing descriptive statistics on dataset
display(df.describe(), df.describe(include='object'))

ID  Year_Birth      Income   Kidhome  Teenhome   Recency  \
count   2240.000    2240.000    2216.000  2240.000  2240.000  2240.000   
mean    5592.160    1968.806   52247.251     0.444     0.506    49.109   
std     3246.662      11.984   25173.077     0.538     0.545    28.962   
min        0.000    1893.000    1730.000     0.000     0.000     0.000   
25%     2828.250    1959.000   35303.000     0.000     0.000    24.000   
50%     5458.500    1970.000   51381.500     0.000     0.000    49.000   
75%     8427.750    1977.000   68522.000     1.000     1.000    74.000   
max    11191.000    1996.000  666666.000     2.000     2.000    99.000   

       MntWines  MntFruits  MntMeatProducts  MntFishProducts  \
count  2240.000   2240.000         2240.000         2240.000   
mean    303.936     26.302          166.950           37.525   
std     336.597     39.773          225.715           54.629   
min       0.000      0.000            0.000            0.000   
25%      23.750      1.000           16.000            3.000   
50%     173.500      8.000           67.000           12.000   
75%     504.250     33.000          232.000           50.000   
max    1493.000    199.000         1725.000          259.000   

       MntSweetProducts  MntGoldProds  NumDealsPurchases  NumWebPurchases  \
count          2240.000      2240.000           2240.000         2240.000   
mean             27.063        44.022              2.325            4.085   
std              41.280        52.167              1.932            2.779   
min               0.000         0.000              0.000            0.000   
25%               1.000         9.000              1.000            2.000   
50%               8.000        24.000              2.000            4.000   
75%              33.000        56.000              3.000            6.000   
max             263.000       362.000             15.000           27.000   

       NumCatalogPurchases  NumStorePurchases  NumWebVisitsMonth  \
count             2240.000           2240.000           2240.000   
mean                 2.662              5.790              5.317   
std                  2.923              3.251              2.427   
min                  0.000              0.000              0.000   
25%                  0.000              3.000              3.000   
50%                  2.000              5.000              6.000   
75%                  4.000              8.000              7.000   
max                 28.000             13.000             20.000   

       AcceptedCmp3  AcceptedCmp4  AcceptedCmp5  AcceptedCmp1  AcceptedCmp2  \
count      2240.000      2240.000      2240.000      2240.000      2240.000   
mean          0.073         0.075         0.073         0.064         0.013   
std           0.260         0.263         0.260         0.245         0.115   
min           0.000         0.000         0.000         0.000         0.000   
25%           0.000         0.000         0.000         0.000         0.000   
50%           0.000         0.000         0.000         0.000         0.000   
75%           0.000         0.000         0.000         0.000         0.000   
max           1.000         1.000         1.000         1.000         1.000   

       Complain  Z_CostContact  Z_Revenue  Response  
count  2240.000         2240.0     2240.0  2240.000  
mean      0.009            3.0       11.0     0.149  
std       0.096            0.0        0.0     0.356  
min       0.000            3.0       11.0     0.000  
25%       0.000            3.0       11.0     0.000  
50%       0.000            3.0       11.0     0.000  
75%       0.000            3.0       11.0     0.000  
max       1.000            3.0       11.0     1.000

Education Marital_Status Dt_Customer
count         2240           2240        2240
unique           5              8         663
top     Graduation        Married  31-08-2012
freq          1127            864          12

From dataset audit above, we can observe these findings:  
1. `Supermarket Customers` dataset consists of 29 columns (including `index` column) and 2216 rows.
2. Several of those columns have mismatched values and types. We will fix it in the next step.
3. Highest scale of this dataset located in `Income` column, from 1730 to 666666.
3. `Income` column has missing values, represented by 'nan' and amount to 24 data or 1% of its total. This is considered insignificant and may be dropped after we analyze it in the next stage. 
4. `Year_Birth` and `Dt_Customer` columns are supposed to categorized as datetime type, based on their values. These can also be grouped into new columns based on a categorical/ordinal typing to provide additional context in our analysis.
5. `Education` and `Marital_Status` columns have ambiguous data, such as '2n Cycle' and 'YOLO'.
6. `Z_CostContact` and `Z_Revenue` columns have no documentation in Data Dictionary.

# Data Wrangling

---

Before delving further into the analysis, we need to manage and convert our data in ways/formats that would made it easier to understand. Such procedure is called Data Wrangling. All kinds of data issues and anomalies found in this step are going to be processed based on "domain knowledge" and statistical approach towards them. 

### Duplicate Issues

In [68]:
# Checking any data duplicates in dataset
mask = df.duplicated()
df[mask]

Empty DataFrame
Columns: [ID, Year_Birth, Education, Marital_Status, Income, Kidhome, Teenhome, Dt_Customer, Recency, MntWines, MntFruits, MntMeatProducts, MntFishProducts, MntSweetProducts, MntGoldProds, NumDealsPurchases, NumWebPurchases, NumCatalogPurchases, NumStorePurchases, NumWebVisitsMonth, AcceptedCmp3, AcceptedCmp4, AcceptedCmp5, AcceptedCmp1, AcceptedCmp2, Complain, Z_CostContact, Z_Revenue, Response]
Index: []

No duplicates detected in this dataset.

### Interpretability Issues

In [69]:
# Listing dataset's columns
df.columns.tolist()

['ID',
 'Year_Birth',
 'Education',
 'Marital_Status',
 'Income',
 'Kidhome',
 'Teenhome',
 'Dt_Customer',
 'Recency',
 'MntWines',
 'MntFruits',
 'MntMeatProducts',
 'MntFishProducts',
 'MntSweetProducts',
 'MntGoldProds',
 'NumDealsPurchases',
 'NumWebPurchases',
 'NumCatalogPurchases',
 'NumStorePurchases',
 'NumWebVisitsMonth',
 'AcceptedCmp3',
 'AcceptedCmp4',
 'AcceptedCmp5',
 'AcceptedCmp1',
 'AcceptedCmp2',
 'Complain',
 'Z_CostContact',
 'Z_Revenue',
 'Response']

In [70]:
# Showing Data Dictionary
print(dataDict)

Supermarket Customers Data Dictionary

People

● ID: Customer's unique identifier
● Year_Birth: Customer's birth year
● Education: Customer's education level
● Marital_Status: Customer's marital status
● Income: Customer's yearly household income
● Kidhome: Number of children in customer's household
● Teenhome: Number of teenagers in customer's household
● Dt_Customer: Date of customer's enrollment with the company
● Recency: Number of days since customer's last purchase
● Complain: 1 if the customer complained in the last 2 years, 0 otherwise

Products

● MntWines: Amount spent on wine in last 2 years
● MntFruits: Amount spent on fruits in last 2 years
● MntMeatProducts: Amount spent on meat in last 2 years
● MntFishProducts: Amount spent on fish in last 2 years
● MntSweetProducts: Amount spent on sweets in last 2 years
● MntGoldProds: Amount spent on gold in last 2 years

Promotion

● NumDealsPurchases: Number of purchases made with a discount
● AcceptedCmp1: 1 if the customer accept

In [71]:
# Reordering, renaming, & removing columns
cols = ['ID',
 'Year_Birth',
 'Education',
 'Marital_Status',
 'Income',
 'Kidhome',
 'Teenhome',
 'Dt_Customer',
 'Recency',
 'Complain',
 'MntWines',
 'MntFruits',
 'MntMeatProducts',
 'MntFishProducts',
 'MntSweetProducts',
 'MntGoldProds',
 'NumDealsPurchases',
 'AcceptedCmp1',
 'AcceptedCmp2',
 'AcceptedCmp3',
 'AcceptedCmp4',
 'AcceptedCmp5',
 'Response',
 'NumWebPurchases',
 'NumCatalogPurchases',
 'NumStorePurchases',
 'NumWebVisitsMonth',]
df = pd.DataFrame(data=df[cols])
df.rename(mapper={'Response': 'AcceptedCmp6'}, axis=1, inplace=True)

### Data Type Issues

In [72]:
# Converting columns' original type to their appropriate type...
# ...for later use in data profiling/EDA:
convert_dict = {'ID': 'object',
                'Education': 'object',
                'Marital_Status': 'object',
                'Kidhome': 'object',
                'Teenhome': 'object',
                'Complain': 'object',
                'AcceptedCmp1': 'object',
                'AcceptedCmp2': 'object',
                'AcceptedCmp3': 'object',
                'AcceptedCmp4': 'object',
                'AcceptedCmp5': 'object',
                'AcceptedCmp6': 'object'}
df = df.astype(convert_dict)

# Converting 'Year_Birth' with integer type to datetime type...
# ...in acccordance with Data Dictionary ("● Year_Birth: Customer's birth year")
df['Year_Birth'] = pd.to_datetime(df['Year_Birth'], format='%Y')

# Converting 'Dt_Customer' with object type to datetime type...
# ...in acccordance with Data Dictionary ("● Dt_Customer: Date of customer's enrollment with the company")
df['Dt_Customer'] = pd.to_datetime(df['Dt_Customer'], dayfirst=True)

### Inconsistency & Ambiguousness Issues

In [73]:
# Detecting inconsistent data label
display(df['Education'].unique(), df.groupby(by='Education').agg(func={'ID': 'count'}))

array(['Graduation', 'PhD', 'Master', 'Basic', '2n Cycle'], dtype=object)

ID
Education       
2n Cycle     203
Basic         54
Graduation  1127
Master       370
PhD          486

`Education` column is using inconsistent naming & labeling. Therefore, we are going to use International Standard Classification of Education (ISCED) to rename these label while maintaining the same amount of data.

In [74]:
# Replacing inconsistent label
df['Education'].replace({'Graduation': 'Bachelor',
                         'PhD': 'Doctorate',
                         'Basic': "Primary",
                         '2n Cycle': "Secondary"}, inplace=True)

df.groupby(by='Education').agg(func={'ID': 'count'})

ID
Education      
Bachelor   1127
Doctorate   486
Master      370
Primary      54
Secondary   203

In [75]:
# Detecting ambiguous label
display(df['Marital_Status'].unique(), df.groupby(by='Marital_Status').agg(func={'ID': 'count'}))

array(['Single', 'Together', 'Married', 'Divorced', 'Widow', 'Alone',
       'Absurd', 'YOLO'], dtype=object)

ID
Marital_Status     
Absurd            2
Alone             3
Divorced        232
Married         864
Single          480
Together        580
Widow            77
YOLO              2

We cannot apply the same procedure on `Marital_Status` column, since there is no accepted standard and also varies between regions and countries. But in retail industry such as Supermarket, they simply views the marital status of their customer based on whether they are together with their partner or not, since this ties to grouping for their `Income` category later on (dual or single income family).

Ambiguous label are replaced with 'Other' since they cannot be grouped either with 'Single' or 'Together'.

In [76]:
# Replacing & regrouping inconsistent label
df['Marital_Status'].replace({'Married': 'Together',
                              'Divorced': 'Single',
                              'Widow': 'Single',
                              'Alone': "Single",
                              'Absurd': 'Other',
                              'YOLO': 'Other'}, inplace=True)

df.groupby(by='Marital_Status').agg(func={'ID': 'count'})

ID
Marital_Status      
Other              4
Single           792
Together        1444

In [77]:
# Detecting inconsistent column label
df.columns.to_list()

['ID',
 'Year_Birth',
 'Education',
 'Marital_Status',
 'Income',
 'Kidhome',
 'Teenhome',
 'Dt_Customer',
 'Recency',
 'Complain',
 'MntWines',
 'MntFruits',
 'MntMeatProducts',
 'MntFishProducts',
 'MntSweetProducts',
 'MntGoldProds',
 'NumDealsPurchases',
 'AcceptedCmp1',
 'AcceptedCmp2',
 'AcceptedCmp3',
 'AcceptedCmp4',
 'AcceptedCmp5',
 'AcceptedCmp6',
 'NumWebPurchases',
 'NumCatalogPurchases',
 'NumStorePurchases',
 'NumWebVisitsMonth']

In [78]:
# Renaming inconsistent column label
df.rename(mapper={'MntMeatProducts': 'MntMeats', 
                  'MntFishProducts': 'MntFish', 
                  'MntSweetProducts': 'MntSweets', 
                  'MntGoldProds': 'MntGolds'},
                  axis=1, inplace=True)

### Missing Data Issues

In [79]:
# Analyzing missing data/values
mask = pd.isna(df['Income'])
df[mask].reset_index()

index     ID Year_Birth  Education Marital_Status  Income Kidhome  \
0      10   1994 1983-01-01   Bachelor       Together     NaN       1   
1      27   5255 1986-01-01   Bachelor         Single     NaN       1   
2      43   7281 1959-01-01  Doctorate         Single     NaN       0   
3      48   7244 1951-01-01   Bachelor         Single     NaN       2   
4      58   8557 1982-01-01   Bachelor         Single     NaN       1   
5      71  10629 1973-01-01  Secondary       Together     NaN       1   
6      90   8996 1957-01-01  Doctorate       Together     NaN       2   
7      91   9235 1957-01-01   Bachelor         Single     NaN       1   
8      92   5798 1973-01-01     Master       Together     NaN       0   
9     128   8268 1961-01-01  Doctorate       Together     NaN       0   
10    133   1295 1963-01-01   Bachelor       Together     NaN       0   
11    312   2437 1989-01-01   Bachelor       Together     NaN       0   
12    319   2863 1970-01-01   Bachelor         Single     NaN       1   
13   1379  10475 1970-01-01     Master       Together     NaN       0   
14   1382   2902 1958-01-01   Bachelor       Together     NaN       1   
15   1383   4345 1964-01-01  Secondary         Single     NaN       1   
16   1386   3769 1972-01-01  Doctorate       Together     NaN       1   
17   2059   7187 1969-01-01     Master       Together     NaN       1   
18   2061   1612 1981-01-01  Doctorate         Single     NaN       1   
19   2078   5079 1971-01-01   Bachelor       Together     NaN       1   
20   2079  10339 1954-01-01     Master       Together     NaN       0   
21   2081   3117 1955-01-01   Bachelor         Single     NaN       0   
22   2084   5250 1943-01-01     Master         Single     NaN       0   
23   2228   8720 1978-01-01  Secondary       Together     NaN       0   

   Teenhome Dt_Customer  Recency Complain  MntWines  MntFruits  MntMeats  \
0         0  2013-11-15       11        0         5          5         6   
1         0  2013-02-20       19        0         5          1         3   
2         0  2013-11-05       80        0        81         11        50   
3         1  2014-01-01       96        0        48          5        48   
4         0  2013-06-17       57        0        11          3        22   
5         0  2012-09-14       25        0        25          3        43   
6         1  2012-11-19        4        0       230         42       192   
7         1  2014-05-27       45        0         7          0         8   
8         0  2013-11-23       87        0       445         37       359   
9         1  2013-07-11       23        0       352          0        27   
10        1  2013-08-11       96        0       231         65       196   
11        0  2013-06-03       69        0       861        138       461   
12        2  2013-08-23       67        0       738         20       172   
13        1  2013-04-01       39        0       187          5        65   
14        1  2012-09-03       87        0        19          4        12   
15        1  2014-01-12       49        0         5          1         9   
16        0  2014-03-02       17        0        25          1        13   
17        1  2013-05-18       52        0       375         42        48   
18        0  2013-05-31       82        0        23          0        15   
19        1  2013-03-03       82        0        71          1        16   
20        1  2013-06-23       83        0       161          0        22   
21        1  2013-10-18       95        0       264          0        21   
22        0  2013-10-30       75        0       532        126       490   
23        0  2012-08-12       53        0        32          2      1607   

    MntFish  MntSweets  MntGolds  NumDealsPurchases AcceptedCmp1 AcceptedCmp2  \
0         0          2         1                  1            0            0   
1         3        263       362                  0            0            0   
2         3          2        39  

Missing value (MV) on `Income` appears to be unrelated to all columns (i.e. happens randomly).  
Except on `Complain`, `AcceptedCmp2`, `AcceptedCmp3`, which has similar patterns (all of them have zero values).

In [80]:
# Further analyzing relationship of columns with MV
mask1 = (df['Complain']) == 0
mask2 = (df['AcceptedCmp2']) == 0
mask3 = (df['AcceptedCmp3']) == 0

display(df.loc[mask1, ['Income', 'Complain']], df.loc[mask2, ['Income', 'AcceptedCmp2']], df.loc[mask3, ['Income', 'AcceptedCmp3']])

Income Complain
0     58138.0        0
1     46344.0        0
2     71613.0        0
3     26646.0        0
4     58293.0        0
...       ...      ...
2235  61223.0        0
2236  64014.0        0
2237  56981.0        0
2238  69245.0        0
2239  52869.0        0

[2219 rows x 2 columns]

Income AcceptedCmp2
0     58138.0            0
1     46344.0            0
2     71613.0            0
3     26646.0            0
4     58293.0            0
...       ...          ...
2235  61223.0            0
2236  64014.0            0
2237  56981.0            0
2238  69245.0            0
2239  52869.0            0

[2210 rows x 2 columns]

Income AcceptedCmp3
0     58138.0            0
1     46344.0            0
2     71613.0            0
3     26646.0            0
4     58293.0            0
...       ...          ...
2235  61223.0            0
2236  64014.0            0
2237  56981.0            0
2238  69245.0            0
2239  52869.0            0

[2077 rows x 2 columns]

On `Complain`, `AcceptedCmp2`, and `AcceptedCmp3` with zero values, it appears to be unrelated with `Income`, because those columns with zero values also has `Income` with values other than zero.  
Therefore, MV on `Income` column can be classified as <u>Missing Completely At Random (MCAR)</u>.
But we would miss valuable information if we drop such data. We can simply impute a new label i.e. 0 into them. This wouldn't disturb the ditribution of our dataset since the missing value percentage is insignificant

In [81]:
# Filling missing values on 'Income' column
df.fillna(value=0, inplace=True)

### Data Type Issue: `Income`

In [82]:
# Analyzing 'Income' column
df['Income'].unique().tolist()

[58138.0,
 46344.0,
 71613.0,
 26646.0,
 58293.0,
 62513.0,
 55635.0,
 33454.0,
 30351.0,
 5648.0,
 0.0,
 7500.0,
 63033.0,
 59354.0,
 17323.0,
 82800.0,
 41850.0,
 37760.0,
 76995.0,
 33812.0,
 37040.0,
 2447.0,
 58607.0,
 65324.0,
 40689.0,
 18589.0,
 53359.0,
 38360.0,
 84618.0,
 10979.0,
 38620.0,
 40548.0,
 46610.0,
 68657.0,
 49389.0,
 67353.0,
 23718.0,
 42429.0,
 48948.0,
 80011.0,
 20559.0,
 21994.0,
 79941.0,
 41728.0,
 72550.0,
 65486.0,
 79143.0,
 35790.0,
 82582.0,
 66373.0,
 82384.0,
 70287.0,
 27938.0,
 55954.0,
 75777.0,
 66653.0,
 61823.0,
 67680.0,
 70666.0,
 25721.0,
 32474.0,
 88194.0,
 69096.0,
 74854.0,
 66991.0,
 65031.0,
 60631.0,
 28332.0,
 40246.0,
 75251.0,
 75825.0,
 26326.0,
 56046.0,
 29760.0,
 26304.0,
 23559.0,
 81361.0,
 29440.0,
 36138.0,
 50388.0,
 79593.0,
 54178.0,
 42394.0,
 23626.0,
 30096.0,
 47916.0,
 51813.0,
 78497.0,
 50150.0,
 47823.0,
 34554.0,
 85693.0,
 65846.0,
 87195.0,
 24594.0,
 49096.0,
 52413.0,
 38557.0,
 89058.0,
 77298.0,
 68126.

In [83]:
# Converting 'Income' data into appropriate type...
# ...(Integer type because no data with floating point number)
df['Income'] = df['Income'].astype(np.int64)

# Data Enrichment

---

### `Year_Birth` & `Dt_Customer`

# Data Enrichment

---

### `Year_Birth` & `Dt_Customer`

In [84]:
# Creating new column 'Age_Enrolled'...
# ...based on the difference between 'Year_Birth' and 'Dt_Customer'
col = df.pop('Dt_Customer')
df.insert(loc=1, column=col.name, value=col) # Reordering column (Dt_Customer) for ease of interpreting later on
df.insert(loc=3, column='Age_Enrolled', value=df['Dt_Customer'].dt.year - df['Year_Birth'].dt.year)

Next, we are going create customer's grouping based on their `Recency`, total amount (monetary value) spent on `Products`, and `NumWebVisitsMonth` for later use in RFM analysis. Determining the number of group would require advanced statistical method such as clustering analysis. 

But any resulting segments can be ordered from most valuable (highest recency, frequency, and monetary value) to least valuable (lowest recency, frequency, and value). Therefore, we are going to arbitrarily group our customers into 3 segments and simply comparing between the highest valuable segment, segment around the median value, and the lowest segment.

### `Recency`

In [85]:
# Creating new column 'R_Group'
df.insert(loc=10, column='R_Group', value=pd.cut(x=df['Recency'], 
                                                 bins=3, labels=['Recent Customer', 'Ordinary Customer', 'Past Customer']))

### `Monetary`

In [86]:
# Creating new column 'MntTotal'...
# ...Based on the amount of each columns in 'Product'
df.insert(loc=18, column='MntTotal', value=df.iloc[:, 14:20].sum(axis=1))
df['MntTotal'] = df['MntTotal'].astype(np.int64)

# Creating new column 'M_Group' based on IQR of 'MntTotal'
df.insert(loc=19, column='M_Group', value=pd.cut(x=df['MntTotal'], 
                                                 bins=3, labels=['Cheap Customer', 'Moderate Customer', 'Moneymaker Customer']))

### `Frequency`

In [87]:
# Creating new column 'F_Group' based on IQR of 'NumWebVisitsMonth'
df.insert(loc=31, column='F_Group', value=pd.cut(x=df['NumWebVisitsMonth'], 
                                                 bins=3, labels=['Infrequent Customer', 'Regular Customer', 'Frequent Customer']))

In [88]:
# Final dataset audit
print(f'Rows, Columns: {df.shape}')

pd.DataFrame({
    'Name': df.columns.values,
    'Type': df.dtypes.values,
    'N/A (n)': df.isna().sum(),
    'N/A (%)': df.isna().mean().values * 100,
    'Unique': df.nunique().values,
    'Sample': [df[column].unique() for column in df.columns]
}).reset_index()\
    .drop(['index'], axis=1)

Rows, Columns: (2240, 32)


Name            Type  N/A (n)  N/A (%)  Unique  \
0                    ID          object        0      0.0    2240   
1           Dt_Customer  datetime64[ns]        0      0.0     663   
2            Year_Birth  datetime64[ns]        0      0.0      59   
3          Age_Enrolled           int64        0      0.0      61   
4             Education          object        0      0.0       5   
5        Marital_Status          object        0      0.0       3   
6                Income           int64        0      0.0    1975   
7               Kidhome          object        0      0.0       3   
8              Teenhome          object        0      0.0       3   
9               Recency           int64        0      0.0     100   
10              R_Group        category        0      0.0       3   
11             Complain          object        0      0.0       2   
12             MntWines           int64        0      0.0     776   
13            MntFruits           int64        0      0.0     158   
14             MntMeats           int64        0      0.0     558   
15              MntFish           int64        0      0.0     182   
16            MntSweets           int64        0      0.0     177   
17             MntGolds           int64        0      0.0     213   
18             MntTotal           int64        0      0.0     734   
19              M_Group        category        0      0.0       3   
20    NumDealsPurchases           int64        0      0.0      15   
21         AcceptedCmp1          object        0      0.0       2   
22         AcceptedCmp2          object        0      0.0       2   
23         AcceptedCmp3          object        0      0.0       2   
24         AcceptedCmp4          object        0      0.0       2   
25         AcceptedCmp5          object        0      0.0       2   
26         AcceptedCmp6          object        0      0.0       2   
27      NumWebPurchases           int64        0      0.0      15   
28  NumCatalogPurchases           int64        0      0.0      14   
29    NumStorePurchases           int64        0      0.0      14   
30    NumWebVisitsMonth           int64        0      0.0      16   
31              F_Group        category        0      0.0       3   

                                                                                                 Sample  
0   [5524, 2174, 4141, 6182, 5324, 7446, 965, 6177, 4855, 5899, 1994, 387, 2125, 8180, 2569, 2114, 9...  
1   [2012-09-04T00:00:00.000000000, 2014-03-08T00:00:00.000000000, 2013-08-21T00:00:00.000000000, 20...  
2   [1957-01-01T00:00:00.000000000, 1954-01-01T00:00:00.000000000, 1965-01-01T00:00:00.000000000, 19...  
3   [55, 60, 48, 30, 33, 46, 41, 28, 39, 64, 36, 54, 61, 25, 66, 32, 27, 34, 63, 62, 44, 37, 24, 50,...  
4                                                     [Bachelor, Doctorate, Master, Primary, Secondary]  
5                                                                             [Single, Together, Other]  
6   [58138, 46344, 71613, 26646, 58293, 62513, 55635, 33454, 30351, 5648, 0, 7500, 63033, 59354, 173...  
7                                                                                             [0, 1, 2]  
8                                                                                             [0, 1, 2]  
9   [58, 38, 26, 94, 16, 34, 32, 19, 68, 11, 59, 82, 53, 23, 51, 20, 91, 86, 41, 42, 63, 0, 69, 89, ...  
10  ['Ordinary Customer', 'Recent Customer', 'Past Customer']
Categories (3, object): ['Recent Custo...  
11                                                                                               [0, 1]  
12  [635, 11, 426, 173, 520, 235, 76, 14, 28, 5, 6, 194, 233, 3, 1006, 53, 84, 1012, 4, 86, 1, 867, ...  
13  [88, 1, 49, 4, 43, 42, 65, 10, 0, 5, 16, 61, 2, 14, 22, 80, 17, 3, 100, 12, 34, 8, 76, 11, 164, ...  
14  [546, 6, 127, 20, 118, 98, 164, 56, 24, 11, 480, 53, 17, 115, 19, 38, 498, 73, 1725, 86, 102, 27...  
15  [172, 2, 111, 10, 46, 0, 50, 3, 1, 11, 22

# Data Analysis

---

## `Promotion`
Let us revert back to Supermarket's problem statement of <i>low conversion rate</i>. We are going to select the `Promotion` columns, renaming the value based on Data Dictionary for easier interpretation ('Yes' and 'No'), and sizing up the data to see the frequency of each values.

In [89]:
# Measuring frequency of each 'Promotion' campaigns
source = df.iloc[:, 21:27]\
            .replace(to_replace={0: 'Not Accept', 1: 'Accept'})\
            .melt(var_name='Column', value_name='Response')\
            .groupby(by=['Column', 'Response'])\
            .size()\
            .to_frame(name='Count')\
            .reset_index()
display(source)

Column    Response  Count
0   AcceptedCmp1      Accept    144
1   AcceptedCmp1  Not Accept   2096
2   AcceptedCmp2      Accept     30
3   AcceptedCmp2  Not Accept   2210
4   AcceptedCmp3      Accept    163
5   AcceptedCmp3  Not Accept   2077
6   AcceptedCmp4      Accept    167
7   AcceptedCmp4  Not Accept   2073
8   AcceptedCmp5      Accept    163
9   AcceptedCmp5  Not Accept   2077
10  AcceptedCmp6      Accept    334
11  AcceptedCmp6  Not Accept   1906

In [90]:
# Measuring the percentage of 'Yes' responses
round(source[source['Response'] == 'Accept'].reset_index()['Count'] 
/ source.groupby(by='Column').agg(func={'Count': 'sum'}).reset_index()['Count'] * 100).to_frame(name='%')

%
0   6.0
1   1.0
2   7.0
3   7.0
4   7.0
5  15.0

In [91]:
# Visualizing 'Promotion' campaigns using bar chart
chart = alt.Chart(data=source)

base = chart.encode(
    y=alt.Y('Count', axis=alt.Axis(titleAngle=0, titleX=-55)),
    x=alt.X('Response', title=None, axis=None),
    column=alt.Column('Column', title=None),
    color=alt.Color('Response'),
    tooltip=['Column', 'Response', 'Count']
)

base.mark_bar().properties(
    title=alt.Title(
        text="Conversion Rate Ranges Between 1% to 15%",
        subtitle="Frequency of customers' Responses on Supermarket's Campaigns",
        anchor='start',
        font='Calibri',
        fontSize=18,
        offset=20
    ),
    width=150, height=400
)

alt.Chart(...)

To solve this low-rate problem, we shall look first into Supermarket customers' characteristics based on `People` (their demographics), `Product` (amount spent on each kind of products), and `Place` (where they bought it).

## `People`

In [92]:
# Measuring rounded ratio of max-min value in 'Age_Enrolled'...
# ...for later usage in data binning
print(f'''Ratio: {round(df['Age_Enrolled'].max() / df['Age_Enrolled'].min())}''')

# Measuring its median and MAD
median = df['Age_Enrolled'].median()
mad = abs(df['Age_Enrolled'] - df['Age_Enrolled'].median()).median()
print(f'Lower: {median - mad}, Upper: {median + mad}')

# Measuring rounded percentage of customers on those range
mask = (df['Age_Enrolled'] > median - mad) & (df['Age_Enrolled'] < median + mad)
print(f'Percentage: {round(len(df[mask]) / len(df) * 100)}%')

Ratio: 8
Lower: 34.0, Upper: 52.0
Percentage: 49%


In [93]:
#Visualizing 'Age_Enrolled' using binned histogram
alt.Chart(data=df).mark_bar().encode(
    x=alt.X('Age_Enrolled', title='Age Enrolled').bin(step=8),
    y=alt.Y('count()', title='Frequency', axis=alt.Axis(titleAngle=0, titleX=-60)),
    color=alt.Color('count()', title='Frequency').scale(scheme="lightgreyteal",),
    tooltip='count()'
).properties(
    title=alt.Title(
        text="49% of Customers Aged Between 34 to 52",
        subtitle="Distribution of Supermarket Customers' Age",
        anchor='start',
        font='Calibri',
        fontSize=18,
        offset=20
    ),
    width=1000, height=300
)

alt.Chart(...)

In [94]:
# Measuring rounded percentage of customer's 'Education'
df['Education'].value_counts(normalize=True).mul(100).round().to_frame(name='Percentage')

Percentage
Bachelor         50.0
Doctorate        22.0
Master           17.0
Secondary         9.0
Primary           2.0

In [95]:
#Visualizing 'Education' using bar chart
alt.Chart(data=df).mark_bar().encode(
    x=alt.X('Education', title=None, axis=alt.Axis(labelAngle=0), sort='-y'),
    y=alt.Y('count()', title='Frequency', axis=alt.Axis(titleAngle=0, titleX=-60)),
    color=alt.Color('count()', title='Frequency'),
    tooltip='count()'
).properties(title=alt.Title(
    text="50% of Customers have Bachelor Degree",
    subtitle="Distribution of Supermarket Customers' Education",
    anchor='start',
    font='Calibri',
    fontSize=18,
    offset=20
    ),
    width=1000, height=400
)

alt.Chart(...)

In [96]:
alt.Chart(data=df).mark_boxplot().encode(
    x=alt.X('Income')
).properties(title=alt.Title(
    text="Distribution of Supermarket Customers' Income",
    font='Calibri',
    fontSize=18,
    offset=20
    ),
    width=1000, height=100
)

alt.Chart(...)

We can see that 50% of Supermarket customers' income ranges between 35.000 to 68.000 (denoted by the interquartile range), with the median value of 51.075. The distribution skewed to the right, with several outliers detected around the value of 160.000 and also the maximum value of 666.666.

In [97]:
# Measuring proportion percentage of customer's 'Marital_Status'
df['Education'].value_counts(normalize=True).mul(100).round().to_frame(name='Percentage')
source = df.groupby(by='Marital_Status').agg(func={'ID': 'count'}).reset_index().sort_values(by='ID', ascending=False)
source['%'] = source['ID'] / source['ID'].sum()
source.rename(mapper={'Marital_Status': 'Marital Status', 'ID': 'Frequency'}, axis=1, inplace=True)
display(source)

Marital Status  Frequency      %
2       Together       1444  0.645
1         Single        792  0.354
0          Other          4  0.002

In [98]:
# Visualizing 'Marital_Status' using pie chart
base = alt.Chart(source).encode(
    alt.Theta('%', stack=True),
    alt.Color('Marital Status:O', scale= alt.Scale(domain=['Other', 'Single', 'Together'],
                                                 range=['red', 'orange', 'blue'])),
    alt.Tooltip(['Marital Status', 'Frequency'])
).properties(title=alt.Title(
    text="Proportion of Supermarket Customers' Marital Status",
    font='Calibri',
    fontSize=18,
    offset=20
    ),
    width=500
)

pie = base.mark_arc(outerRadius=120)
text = base.mark_text(radius=150, size=15).encode(
    text=alt.Text('%', format='.1%'),
)

pie + text

alt.LayerChart(...)

In [99]:
# Measuring proportion percentage of customer's 'Kidhome'
source = df.groupby(by='Kidhome').agg(func={'ID': 'count'}).reset_index().sort_values(by='ID', ascending=False)
source['%'] = source['ID'] / source['ID'].sum()
source.rename(mapper={'Kidhome': 'Number of Children', 'ID': 'Frequency'}, axis=1, inplace=True)
display(source)

Number of Children  Frequency      %
0                   0       1293  0.577
1                   1        899  0.401
2                   2         48  0.021

In [100]:
# Visualizing 'Kidhome' using pie chart
base = alt.Chart(source).encode(
    alt.Theta('%:Q', stack=True),
    alt.Color('Number of Children:O').scale(scheme='category10'),
    alt.Tooltip(['Number of Children', 'Frequency'])
).properties(title=alt.Title(
    text="Proportion of Supermarket Customers' Number of Children",
    font='Calibri',
    fontSize=18,
    offset=20
    ),
    width=500
)

pie = base.mark_arc(outerRadius=120)
text = base.mark_text(radius=150, size=15).encode(
    text=alt.Text('%', format='.1%'),
)

pie + text

alt.LayerChart(...)

In [101]:
# Measuring proportion percentage of customer's 'Teenhome'
source = df.groupby(by='Teenhome').agg(func={'ID': 'count'}).reset_index().sort_values(by='ID', ascending=False)
source['%'] = source['ID'] / source['ID'].sum()
source.rename(mapper={'Teenhome': 'Number of Teenagers', 'ID': 'Frequency'}, axis=1, inplace=True)
display(source)

Number of Teenagers  Frequency      %
0                    0       1158  0.517
1                    1       1030  0.460
2                    2         52  0.023

In [102]:
# Visualizing 'Teenhome' using pie chart
base = alt.Chart(source).encode(
    alt.Theta('%:Q', stack=True),
    alt.Color('Number of Teenagers:O').scale(scheme='category10'),
    alt.Tooltip(['Number of Teenagers', 'Frequency'])
).properties(title=alt.Title(
    text="Proportion of Supermarket Customers' Number of Teenagers",
    font='Calibri',
    fontSize=18,
    offset=20
    ),
    width=500
)

pie = base.mark_arc(outerRadius=120)
text = base.mark_text(radius=150, size=15).encode(
    text=alt.Text('%', format='.1%'),
)

pie + text

alt.LayerChart(...)

In [103]:
# Measuring proportion percentage of customer's 'Complains'
source = df.groupby(by='Complain').agg(func={'ID': 'count'}).reset_index().sort_values(by='ID', ascending=False)
source['%'] = source['ID'] / source['ID'].sum()
source.rename(mapper={'Complain': 'Complained', 'ID': 'Frequency'}, axis=1, inplace=True)
source.replace(to_replace={0: 'No', 1: 'Yes'}, inplace=True)
display(source)

Complained  Frequency      %
0         No       2219  0.991
1        Yes         21  0.009

In [104]:
# Visualizing 'Complain' using pie chart
base = alt.Chart(source).encode(
    alt.Theta('%:Q', stack=True),
    alt.Color('Complained:O').scale(scheme='category10'),
    alt.Tooltip(['Complained', 'Frequency'])
).properties(title=alt.Title(
    text="Proportion of Supermarket Customers' Who Complained in the Last 2 Years",
    font='Calibri',
    fontSize=18,
    offset=20
    ),
    width=500
)

pie = base.mark_arc(outerRadius=120)
text = base.mark_text(radius=150, size=15).encode(
    text=alt.Text('%', format='.1%'),
)

pie + text

alt.LayerChart(...)

As can be seen from visualizations above, we can conclude that most of our customers:
1. Are between the age of 34 to 52.
2. Have bachelor degree.
3. Have income between 35.000 to 68.000
4. Are either married or together (with their partner).
5. Have no dependents (children or teenagers in their household).
6. Are satisfied with Supermarket (haven't lodged any complaints in the last 2 years).

## `Product`

In [105]:
# Measuring total amount spent on 'Product'
source = df.iloc[:, 12:18].sum().to_frame(name='Total').sort_values(by='Total', ascending=False).reset_index(names='Product')
source['%'] = round(source['Total'] / source['Total'].sum() * 100)
source.replace(to_replace={'MntWines': 'Wines', 'MntMeats': 'Meats', 'MntGolds': 'Golds', 
                           'MntFish': 'Fish', 'MntSweets': 'Sweets', 'MntFruits': 'Fruits'}, inplace=True)
display(source)

Product   Total     %
0   Wines  680816  50.0
1   Meats  373968  28.0
2   Golds   98609   7.0
3    Fish   84057   6.0
4  Sweets   60621   4.0
5  Fruits   58917   4.0

In [106]:
# Visualizing 'Product' using bar chart
alt.Chart(data=source).mark_bar().encode(
    x=alt.X('Product', title=None, axis=alt.Axis(labelAngle=0), sort='-y'),
    y=alt.Y('Total', title='Total', axis=alt.Axis(titleAngle=0, titleX=-60)),
    color=alt.Color('Product', title='Total', legend=None),
    tooltip=['Total', '%']
).properties(title=alt.Title(
    text="50% of Supermarket's Revenue Comes From Wine",
    subtitle="Distribution of Supermarket's Revenue per Product",
    anchor='start',
    font='Calibri',
    fontSize=18,
    offset=20
    ),
    width=1000, height=400
)

alt.Chart(...)

Based on the kinds of products offered by Supermarket, we can also see the potential of bundling some of them as one, and offering a discounted price on them to segments of Supermarket's customers. We will discuss the appropriate segment later on.

In [107]:
# Measuring total amount spent on bundled 'Product'
df.insert(loc=19, column='MntGroceries', value=df[['MntMeats', 'MntFish', 'MntFruits', 'MntSweets']].agg(func='sum', axis='columns'))
source = df[['MntWines', 'MntGolds', 'MntGroceries']].sum().to_frame(name='Total').sort_values(by='Total', ascending=False).reset_index(names='Products')
source['%'] = source['Total'] / source['Total'].sum()
source.replace(to_replace={'MntWines': 'Wines', 'MntGroceries': 'Groceries', 'MntGolds': 'Golds'}, inplace=True)
display(source)

Products   Total      %
0      Wines  680816  0.502
1  Groceries  577563  0.426
2      Golds   98609  0.073

In [108]:
# Visualizing bundled 'Product' using pie chart
base = alt.Chart(source).encode(
    alt.Theta('%', stack=True),
    alt.Color('Products').scale(scheme='category10'),
    alt.Tooltip(['Products', 'Total'])
).properties(title=alt.Title(
    text="Proportion of Supermarket Product's Revenue (Bundled)",
    font='Calibri',
    fontSize=18,
    offset=20
    ),
    width=500
)

pie = base.mark_arc(outerRadius=120)
text = base.mark_text(radius=150, size=15).encode(
    text=alt.Text('%', format='.1%'),
)

pie + text

alt.LayerChart(...)

## `Place`

In [109]:
# Measuring total amount of transactions per 'place'
source = df.iloc[:, 28:31].sum().to_frame(name='Total').sort_values(by='Total', ascending=False).reset_index(names='Place')
source['%'] = source['Total'] / source['Total'].sum()
source.replace(to_replace={'NumStorePurchases': 'Store', 'NumWebPurchases': 'Website', 'NumCatalogPurchases': 'Catalog'}, inplace=True)
display(source)

Place  Total      %
0    Store  12970  0.462
1  Website   9150  0.326
2  Catalog   5963  0.212

In [110]:
# Visualizing 'Place' using pie chart
base = alt.Chart(source).encode(
    alt.Theta('%', stack=True),
    alt.Color('Place').scale(scheme='category10'),
    alt.Tooltip(['Place', 'Total'])
).properties(title=alt.Title(
    text="Proportion of Supermarket Transaction per Location",
    font='Calibri',
    fontSize=18,
    offset=20
    ),
    width=500
)

pie = base.mark_arc(outerRadius=120)
text = base.mark_text(radius=150, size=15).encode(
    text=alt.Text('%', format='.1%'),
)

pie + text

alt.LayerChart(...)

Kategori dataset `Place` juga menyertakan `NumWebVisitsMonth`, sehingga memungkinkan kita untuk melakukan analisis RFM atau <i>Recency, Monetary, & Frequency</i> berdasarkan tiga kolom pada dataset, yakni:

1. <b>R</b> = `Recency` atau sejak kapan pelanggan bertransaksi dengan Supermarket, 
2. <b>F</b> = `NumWebVisitsMonth` atau frekuensi kunjungan tiap pelanggan ke website Supermarket dalam kurun waktu 1 bulan terakhir, dan
3. <b>M</b> = `MntTotal` atau jumlah unit moneter yang digunakan pelanggan untuk membeli produk dari Supermarket (dengan kata lain, pendapatan bagi Supermarket).

Secara keseluruhan, kombinasi RFM dapat kita interpretasikan sebagai tingkatan pelanggan yang paling sering berkunjung ke situs Supermarket, paling sering melakukan transaksi melalui media ini, dan paling besar memberikan pendapatan bagi Supermarket, hingga tingkatan sebaliknya.

Seperti yang telah disampaikan sebelumnya, segmentasi berdasarkan RFM dapat dibentuk mulai urutan tertinggi hingga terendah, dan pengguna analisis ini tentu akan lebih tertarik untuk berfokus pada <i>Most Valuable Segment</i> (segmen tertinggi). apakah analisis ini dapat diterapkan pada Supermarket, dapat kita lihat pada tabel berikut:

In [111]:
# Grouping RFM segments
source = df.groupby(['R_Group', 'F_Group', 'M_Group']).agg(func={'ID': 'count'}).reset_index()
source.rename(mapper={'R_Group': 'R Group', 'F_Group': 'F Group', 'M_Group': 'M Group', 'ID': 'Frequency'}, axis=1, inplace=True)
source.sort_values(by='Frequency', ascending=False)

R Group              F Group              M Group  Frequency
0     Recent Customer  Infrequent Customer       Cheap Customer        354
9   Ordinary Customer  Infrequent Customer       Cheap Customer        347
18      Past Customer  Infrequent Customer       Cheap Customer        337
3     Recent Customer     Regular Customer       Cheap Customer        288
21      Past Customer     Regular Customer       Cheap Customer        254
12  Ordinary Customer     Regular Customer       Cheap Customer        253
19      Past Customer  Infrequent Customer    Moderate Customer        116
10  Ordinary Customer  Infrequent Customer    Moderate Customer        114
1     Recent Customer  Infrequent Customer    Moderate Customer        109
4     Recent Customer     Regular Customer    Moderate Customer         14
2     Recent Customer  Infrequent Customer  Moneymaker Customer         12
22      Past Customer     Regular Customer    Moderate Customer         11
11  Ordinary Customer  Infrequent Customer  Moneymaker Customer         11
20      Past Customer  Infrequent Customer  Moneymaker Customer         10
6     Recent Customer    Frequent Customer       Cheap Customer          3
15  Ordinary Customer    Frequent Customer       Cheap Customer          3
24      Past Customer    Frequent Customer       Cheap Customer          2
13  Ordinary Customer     Regular Customer    Moderate Customer          2
17  Ordinary Customer    Frequent Customer  Moneymaker Customer          0
16  Ordinary Customer    Frequent Customer    Moderate Customer          0
14  Ordinary Customer     Regular Customer  Moneymaker Customer          0
8     Recent Customer    Frequent Customer  Moneymaker Customer          0
7     Recent Customer    Frequent Customer    Moderate Customer          0
23      Past Customer     Regular Customer  Moneymaker Customer          0
5     Recent Customer     Regular Customer  Moneymaker Customer          0
25      Past Customer    Frequent Customer    Moderate Customer          0
26      Past Customer    Frequent Customer  Moneymaker Customer          0

In [112]:
# Measuring percentage of 'Infrequent Customers'
source.groupby(['F Group']).agg(func={'Frequency': 'sum'})['Frequency'].values\
      / source.groupby(['F Group']).agg(func={'Frequency': 'sum'})['Frequency'].sum() * 100

array([62.94642857, 36.69642857,  0.35714286])

In [113]:
# Visualizing RFM segments using bar chart
alt.Chart(data=source).mark_bar().encode(
    x=alt.X('Segment:O', title=None, axis=alt.Axis(labelAngle=0), sort='-y'),
    y=alt.Y('Frequency', title='Total', axis=alt.Axis(titleAngle=0, titleX=-60)),
    color='Group:N',
    tooltip=['R Group', 'F Group', 'M Group', 'Frequency']
).transform_fold(
    ['R Group', 'F Group', 'M Group'],
    as_=['Group', 'Segment']
).properties(title=alt.Title(
    text='''62% of Supermarket Customers Categorized as "Infrequent Customer"''',
    subtitle="Distribution of Supermarket Customer's RFM Segmentation",
    anchor='start',
    font='Calibri',
    fontSize=18,
    offset=20
    ),
    width=1000, height=400
)

alt.Chart(...)

Apabila Supermarket melakukan promosi melalui situs websitenya, maka hal ini dapat dinilai sebagai tindakan yang kurang efektif, karena mayoritas pelanggannya justru dikategorikan sebagai 'Infrequent Customer' dan tidak sering mengakses situs resmi Supermarket. Mungkin dapat dikatakan inilah salah satu penyebab mengapa tingkat konversi pelanggan Supermarket yang ditunjukkan dalam kategori dataset `Promotion` selalu bernilai rendah.

# Conclusion

---

Dari analisis yang telah dilakukan, kita dapat membuat kesimpulan berikut mengenai mayoritas karakteristik dan kesamaan antara pelanggan Supermarket:
1. Berada di rentang usia antara 34 hingga 52
2. Bergelar sarjana.
3. Memiliki pendapatan antara 35.000 hingga 68.000
4. Status mereka telah menikah ataupun hidup bersama pasangannya.
5. Tidak memiliki tanggungan anak ataupun remaja.
6. Puas dengan kinerja Supermarket (tidak memberikan komplain dalam kurun waktu 2 tahun terakhir)
7. Nominal pembelian produk `Wines` bernilai paling besar.
8. Melakukan transaksi secara langsung di toko fisik Supermarket.

### Recommendation

1. Menawarkan promosi harga diskon `Wines` pada kombinasi segmen mayoritas pelanggan; semisal menawarkannya pada pelanggan yang telah menikah/hidup dengan pasangan dan tidak memiliki tanggungan anak/remaja. Secara 'domain knowledge', gaya hidup segmen tersebut mengonsumsi produk `Wine` secara rutin, sehingga diharapkan mereka akan menerima penawaran promosi ini dan kedepannya akan meningkatkan pendapatan dari Supermarket.

2. Menawarkan promosi harga diskon berdasarkan 'bundled product' pada segmen potensial yang sesuai; semisal menawarkannya pada pelanggan yang memiliki tanggungan anak/remaja. Produk `Sweets` yang disertakan pada 'bundled product' akan menjadi daya tarik bagi pelanggan untuk menerima tawaran promosi Supermarket. Hal ini juga dilakukan untuk memaksimalkan potensi Supermarket, dan tidak hanya berfokus pada satu produk tertentu yang paling berkontribusi.

3. Dan juga sebaiknya promosi-promosi tersebut dilakukan langsung di toko fisik Supermarket, tidak melalui media website ataupun katalog. Selain faktor biaya promosi yang mungkin relatif besar, dapat dilihat bahwa mayoritas pelanggan Supermarket lebih sering melakukan transaksinya secara langsung.

Dengan berfokus pada jenis `People`, `Product`, dan `Place` tertentu, diharapkan tingkat konversi Supermarket pada `Promotion` berikutnya bisa meningkat.